In [16]:
import dualcodec

In [17]:
# huggingface-cli download facebook/w2v-bert-2.0 --local-dir w2v-bert-2.0                        
# huggingface-cli download amphion/dualcodec --local-dir dualcodec_ckpts
w2v_path = "./w2v-bert-2.0"
dualcodec_model_path = "./dualcodec_ckpts"

In [18]:
dualcodec_model = dualcodec.get_model("12hz_v1", dualcodec_model_path)
inference = dualcodec.Inference(dualcodec_model=dualcodec_model, dualcodec_path=dualcodec_model_path, w2v_path=w2v_path, device='cpu')

/Users/lijiaqi18/miniconda3/lib/python3.12/site-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)


Loading model from ./dualcodec_ckpts/dualcodec_12hz_16384_4096.safetensors
Model loaded


/Users/lijiaqi18/github/DualCodec/dualcodec/inference_with_semantic.py:38: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  stat_mean_var = torch.load(meanvar_path)


In [23]:
# do inference for English example wav
import torchaudio
audio, sr = torchaudio.load('example_wav_en.wav')
# resample
audio = torchaudio.functional.resample(audio, sr, 24000)
audio = audio.reshape(1,1,-1)
# extract codes
semantic_codes, acoustic_codes = inference.encode(audio, n_quantizers=8)
# produce output audio
out_audio = dualcodec_model.decode_from_codes(semantic_codes, acoustic_codes)

In [24]:
from IPython.display import Audio, display
# Play the input audio
print("Input audio")
display(Audio(audio.cpu().numpy().squeeze(), rate=24000))
# Play the output audio
print("Output audio (8vq)")
Audio(out_audio.cpu().numpy().squeeze(), rate=24000)

Input audio


Output audio


In [30]:
# see the shape of codes
print("semantic_codes shape:", semantic_codes.shape)
print("max semantic code:", semantic_codes.max()) # the codebook size for semantic code is 16384
print("acoustic_codes shape:", acoustic_codes.shape)
print("max acoustic code:", acoustic_codes.max()) # the codebook size for acoustic code is 1024(25hz_v1) and 4096(12hz_v1)

semantic_codes shape: torch.Size([1, 1, 99])
max semantic code: tensor(16003)
acoustic_codes shape: torch.Size([1, 7, 99])
max acoustic code: tensor(4095)


In [ ]:
# see the difference with different number of quantizers
for n_q in [1, 2, 4, 8]:
    # decode from codes
    out_audio = dualcodec_model.decode_from_codes(semantic_codes, acoustic_codes[:, :n_q])
    print(f"n_quantizers={n_q}")
    display(Audio(out_audio.cpu().numpy().squeeze(), rate=24000))

n_quantizers=1


n_quantizers=2


n_quantizers=4


n_quantizers=8


In [27]:
# for ZH example
audio, sr = torchaudio.load('example_wav_zh.wav')
# resample
audio = torchaudio.functional.resample(audio, sr, 24000)
audio = audio.reshape(1,1,-1)
# extract codes
semantic_codes, acoustic_codes = inference.encode(audio, n_quantizers=8)
# produce output audio
out_audio = dualcodec_model.decode_from_codes(semantic_codes, acoustic_codes)

In [28]:
print("Input audio")
display(Audio(audio.cpu().numpy().squeeze(), rate=24000))
print("Output audio (8vq)")
display(Audio(out_audio.cpu().numpy().squeeze(), rate=24000))

Input audio


Output audio (8vq)


In [29]:
# see the difference with different number of quantizers
for n_q in [1, 2, 4, 8]:
    out_audio = dualcodec_model.decode_from_codes(semantic_codes, acoustic_codes[:, :n_q])
    print(f"n_quantizers={n_q}")
    display(Audio(out_audio.cpu().numpy().squeeze(), rate=24000))

n_quantizers=1


n_quantizers=2


n_quantizers=4


n_quantizers=8
